## Investigate how dune toe compares to R_high

In [1]:
%matplotlib inline
%reload_ext autoreload
%autoreload

In [2]:
from IPython.core.debugger import set_trace

import pandas as pd
import numpy as np
import os

import plotly
import plotly.graph_objs as go
import plotly.plotly as py
import plotly.tools as tls
import plotly.figure_factory as ff
import plotly.io as pio

### Load data
Load data from the `./data/interim/` folder and parse into `pandas` dataframes.

In [3]:
def df_from_csv(csv, index_col, data_folder='../data/interim'):
    print('Importing {}'.format(csv))
    return pd.read_csv(os.path.join(data_folder,csv), index_col=index_col)

df_profiles = df_from_csv('profiles.csv', index_col=[0, 1, 2])
df_profile_features = df_from_csv('profile_features.csv', index_col=[0])

impacts = {
    'forecasted': {
        'foreshore_slope_sto06': df_from_csv('impacts_forecasted_foreshore_slope_sto06.csv', index_col=[0]),
        'mean_slope_sto06': df_from_csv('impacts_forecasted_mean_slope_sto06.csv', index_col=[0]),
        },
    'observed': df_from_csv('impacts_observed.csv', index_col=[0])
    }

twls = {
    'forecasted': {
        'foreshore_slope_sto06': df_from_csv('twl_foreshore_slope_sto06.csv', index_col=[0, 1]),
        'mean_slope_sto06':df_from_csv('twl_mean_slope_sto06.csv', index_col=[0, 1]),
    }
}

print('Done!')

Importing profiles.csv


C:\Users\z5189959\AppData\Local\Continuum\anaconda3\lib\site-packages\numpy\lib\arraysetops.py:472: FutureWarning:

elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison



Importing profile_features.csv
Importing impacts_forecasted_foreshore_slope_sto06.csv
Importing impacts_forecasted_mean_slope_sto06.csv
Importing impacts_observed.csv
Importing twl_foreshore_slope_sto06.csv
Importing twl_mean_slope_sto06.csv
Done!


### Compare underpredicted cases

In [39]:
# Find site_ids where the forecast has been underpredicted
set1 = set(impacts['forecasted']['mean_slope_sto06'].query("storm_regime == 'swash'").index.get_level_values('site_id'))
set2 = set(impacts['observed'].query("storm_regime == 'collision'").index.get_level_values('site_id'))
site_ids = list(set1.intersection(set2))

# Get dune toes at these sites and predicted max R_high
df_toes = df_profile_features.loc[site_ids].query('profile_type=="prestorm"').dune_toe_z
df_R_highs = twls['forecasted']['mean_slope_sto06'].loc[site_ids].groupby('site_id')['R_high'].max()

# Join into one dataframe
df_twl_toes = pd.concat([df_toes, df_R_highs],axis=1,sort=True)
df_twl_toes['diff'] = df_twl_toes['R_high'] - df_twl_toes['dune_toe_z']
df_twl_toes.head()


dune_toe_z    R_high      diff
AVOCAn0005       3.306  3.260440 -0.045560
AVOCAn0008       3.507  3.220084 -0.286916
BILG0005         4.807  3.293445 -1.513555
BLUEYS0001       3.064  2.800144 -0.263856
BLUEYS0002       2.929  2.470641 -0.458359

Now let's plot the comparison between our R_high TWL values and the dune toes to see how far off they were.

In [41]:
trace1 = go.Histogram(y=df_twl_toes['diff'].tolist())

layout = go.Layout(
    title='D_low - R_high<br>Observed Collision, Forecasted Swash',
    yaxis=dict(
        title='z (m AHD)'
    ),
    xaxis=dict(
        title='Count'
    ),
    bargap=0.2,
    bargroupgap=0.1
)

g_plot = go.FigureWidget(data=[trace1], layout=layout)
g_plot

FigureWidget({
    'data': [{'type': 'histogram',
              'uid': '75f0d11f-9242-4fc7-b433-1f04e1e37ba6',
              'y': [-0.045560088746212646, -0.28691603912686325,
                    -1.5135547360075963, ..., -0.4613631587476821,
                    -0.5212332930925054, -0.3948507473332721]}],
    'layout': {'bargap': 0.2,
               'bargroupgap': 0.1,
               'title': 'D_low - R_high<br>Observed Collision, Forecasted Swash',
               'xaxis': {'title': 'Count'},
               'yaxis': {'title': 'z (m AHD)'}}
})

The above plot shows that the R_high value for most of the incorrectly forecasted collision regimes, was typically underpredicted by less than 0.5 m.

### Compare overpredicted cases

In [42]:
# Find site_ids where the forecast has been overpredicted
set1 = set(impacts['forecasted']['mean_slope_sto06'].query("storm_regime == 'collision'").index.get_level_values('site_id'))
set2 = set(impacts['observed'].query("storm_regime == 'swash'").index.get_level_values('site_id'))
site_ids = list(set1.intersection(set2))

# Get dune toes at these sites and predicted max R_high
df_toes = df_profile_features.loc[site_ids].query('profile_type=="prestorm"').dune_toe_z
df_R_highs = twls['forecasted']['mean_slope_sto06'].loc[site_ids].groupby('site_id')['R_high'].max()

# Join into one dataframe
df_twl_toes = pd.concat([df_toes, df_R_highs],axis=1,sort=True)
df_twl_toes['diff'] = df_twl_toes['R_high'] - df_twl_toes['dune_toe_z']
df_twl_toes.head()


dune_toe_z    R_high      diff
AVOCAn0004       3.178  3.416988  0.238988
BOOM0004         3.065  3.074980  0.009980
BOOM0011         2.771  6.491824  3.720824
BOOM0012         2.796  3.148087  0.352087
CATHIE0001       2.780  3.522792  0.742792

In [47]:
trace1 = go.Histogram(y=df_twl_toes['diff'].tolist())

layout = go.Layout(
    title='D_low - R_high<br>Observed Swash, Forecasted Collision',
    yaxis=dict(
        title='z (m AHD)'
    ),
    xaxis=dict(
        title='Count'
    ),
    bargap=0.2,
    bargroupgap=0.1
)

g_plot = go.FigureWidget(data=[trace1], layout=layout)
g_plot

FigureWidget({
    'data': [{'type': 'histogram',
              'uid': '4a284474-2be1-4fd7-87d5-25364cc78df4',
              'y': [0.23898814460475037, 0.009980312001434566, 3.720823710344608,
                    ..., 1.5720238663972683, 0.912998680585452, 1.1419977620500927]}],
    'layout': {'bargap': 0.2,
               'bargroupgap': 0.1,
               'title': 'D_low - R_high<br>Observed Swash, Forecasted Collision',
               'xaxis': {'title': 'Count'},
               'yaxis': {'title': 'z (m AHD)'}}
})

The errors when we forecast collision but observe swash are much greater than we we forecast swash and observe collision. For this case, errors in excess of 1.0 m common. Why is this?